# Regresión  con Gradient Boosting


#### Datos de entrenamiento originales: 

$\quad D=\{\mathbf{X},\mathbf{y}\}, \quad \mathbf{X}\in \mathbb{R}^{N \times d}, \quad \mathbf{y} \in \mathbb{R}^N$ 

- Numero de datos de entrenamiento: $N$
- Número de atributos de los datos: $d$

Cada fila de $\mathbf{X}$ contiene un dato de entrenamiento, y la correspondiente fila de $\mathbf{y}$ es su etiqueta:

\begin{equation}
    \mathbf{X} =  
    \begin{bmatrix}
        \mathbf{x}_1 \\
        \mathbf{x}_2 \\
        \vdots \\
        \mathbf{x}_N
   \end{bmatrix}, 
   \quad \mathbf{y}=
    \begin{bmatrix}
    y_1 \\
    y_2 \\
    \vdots \\
    y_N
   \end{bmatrix} 
\end{equation}

#### Gradient Boosting:




#### Hiperparámetros de boosting:
- Número de regresores base


#### Importa modulos

In [1]:
%matplotlib inline
import numpy as np
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import BaggingRegressor

#### Carga base de datos
Importa la base de datos "diabetes" de scikit-learn

In [2]:
from sklearn import datasets
diabetes = datasets.load_diabetes()
X = diabetes.data   
y = diabetes.target

[N,d]=X.shape
print('No. de datos:',N)
print('No. de atributos originales:',d)

No. de datos: 442
No. de atributos originales: 10


#### Estandariza los datos

In [3]:
from sklearn import preprocessing 
estandariza=preprocessing.StandardScaler().fit(X)
X=estandariza.transform(X) 

#### Establece el regresor boosting

In [4]:
from sklearn.ensemble import GradientBoostingRegressor
modelo = GradientBoostingRegressor() 

#### Hiperparámetros óptimos

In [5]:
parametros = {'n_estimators': np.arange(10, 100, 10),
              'learning_rate': np.arange(0.1,1.0,0.1),
              'max_depth': np.arange(2,10,1)}

grid = GridSearchCV(modelo,parametros)
grid.fit(X, y)
vp1=grid.best_params_['n_estimators']
vp2=grid.best_params_['learning_rate']
vp3=grid.best_params_['max_depth']
print('    - no. estimadores:',vp1)
print('    - learning_rate:',vp2)
print('    - no. niveles:',vp3)

    - no. estimadores: 80
    - learning_rate: 0.2
    - no. niveles: 1


#### Establece el modelo con los hiperparámetros óptimos

In [6]:
modelo = GradientBoostingRegressor(n_estimators=vp1, learning_rate=vp2, max_depth=vp3) 

#### Prestaciones del modelo sin bagging

In [7]:
scores=cross_val_score(modelo,X,y,cv=8,scoring='neg_mean_squared_error')

print()
print('- Errores RMS sobre los datos de test de cada fold:')
for k in range(len(scores)):
    print('    fold: %d,   score = %0.4f' % (k,np.sqrt(-scores[k])))
print()
print("- Error RMS medio: %0.4f" % (np.sqrt(-scores.mean())))


- Errores RMS sobre los datos de test de cada fold:
    fold: 0,   score = 52.2891
    fold: 1,   score = 57.5833
    fold: 2,   score = 57.0409
    fold: 3,   score = 52.8530
    fold: 4,   score = 57.2581
    fold: 5,   score = 61.8351
    fold: 6,   score = 63.6020
    fold: 7,   score = 45.9753

- Error RMS medio: 56.3006


#### Entrena el modelo con bagging y analiza sus prestaciones

In [8]:
bagging_modelo = BaggingRegressor(base_estimator=modelo,n_estimators=10)
scores=cross_val_score(bagging_modelo,X,y,cv=8,scoring='neg_mean_squared_error')

print()
print('- Errores RMS sobre los datos de test de cada fold:')
for k in range(len(scores)):
    print('    fold: %d,   score = %0.4f' % (k,np.sqrt(-scores[k])))
print()
print("- Error RMS medio con Bagging: %0.4f" % (np.sqrt(-scores.mean())))


- Errores RMS sobre los datos de test de cada fold:
    fold: 0,   score = 52.6745
    fold: 1,   score = 57.2072
    fold: 2,   score = 55.8509
    fold: 3,   score = 53.2465
    fold: 4,   score = 55.5208
    fold: 5,   score = 60.3238
    fold: 6,   score = 61.7950
    fold: 7,   score = 45.5198

- Error RMS medio con Bagging: 55.4684
